In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [42]:
import time
import datetime
import re
import urllib
from bs4 import BeautifulSoup
from random import randint
import pyLDAvis.gensim
from pprint import pprint

In [3]:
initial_date_str = '1 Jan 2018'
initial_date = datetime.datetime.strptime(initial_date_str, '%d %b %Y')
final_date_str = '13 Jun 2018'

final_date = datetime.datetime.strptime(final_date_str, '%d %b %Y')
current_date = initial_date

In [4]:
tweets_list = []
while current_date < final_date :        
    aux_list = open('Tweets/' + current_date.strftime("%Y-%m-%d") + '_trump.txt',encoding='UTF-8').read().split('\n')
    aux_list = [current_date.strftime("%Y-%m-%d") + ', ' + row for row in aux_list]
    tweets_list.extend(aux_list)
    current_date = current_date + datetime.timedelta(days=1)

In [5]:
tweets_list[6500]

'2018-04-15, JTStevison, https://twitter.com/JTStevison/status/985656472687259649, 1, 11, 4, Perfect. <img class="Emoji Emoji--forText" src="https://abs.twimg.com/emoji/v2/72x72/1f602.png" draggable="false" alt="😂" title="Face with tears of joy" aria-label="Emoji: Face with tears of joy"><img class="Emoji Emoji--forText" src="https://abs.twimg.com/emoji/v2/72x72/1f602.png" draggable="false" alt="😂" title="Face with tears of joy" aria-label="Emoji: Face with tears of joy"><a href="/hashtag/DonaldTrump?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b><strong>DonaldTrump</strong></b></a> <a href="/hashtag/Syria?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>Syria</b></a> <a href="/hashtag/SyrianStrikes?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>SyrianStrikes</b></a> <a href="/hashtag/Trump?src=hash" data-qu

In [6]:
def add_space_between_a_tags(html):
    pos_1 = html.find('<a')
    while pos_1 != -1:
        html = html[:pos_1] + ' ' + html[pos_1:]
        pos_1 = html.find('<a',pos_1+2)
        
    pos_1 = html.find('</a>')
    while pos_1 != -1:
        html = html[:pos_1+4] + ' ' + html[pos_1+4:]
        #if len(html) == html.find('</a>',pos_1 + 4)
        pos_1 = html.find('</a>',pos_1+4)
        
    return html

In [7]:
print(add_space_between_a_tags(tweets_list[9870]))

2018-06-09, reggaerapstarCP, https://twitter.com/reggaerapstarCP/status/1005393266530021379, 0, 1, 3, Remember this?This This  <a href="/hashtag/Original?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>Original</b></a>   <a href="/hashtag/hand?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>hand</b></a>   <a href="/hashtag/painting?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>painting</b></a>   <a href="/hashtag/handdesigned?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>handdesigned</b></a>   <a href="/hashtag/usa?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>usa</b></a>   <a href="/hashtag/presidenttrump?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link j

In [8]:
print(tweets_list[9870])

2018-06-09, reggaerapstarCP, https://twitter.com/reggaerapstarCP/status/1005393266530021379, 0, 1, 3, Remember this?This This <a href="/hashtag/Original?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>Original</b></a> <a href="/hashtag/hand?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>hand</b></a> <a href="/hashtag/painting?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>painting</b></a> <a href="/hashtag/handdesigned?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>handdesigned</b></a> <a href="/hashtag/usa?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir="ltr"><s>#</s><b>usa</b></a> <a href="/hashtag/presidenttrump?src=hash" data-query-source="hashtag_click" class="twitter-hashtag pretty-link js-nav" dir=

In [9]:
def get_hashtags(tweet):
    hashtags = []
    pos = tweet.find('#')
    while pos != -1:
        pos_aux = tweet.find(" ",pos)
        if pos_aux == -1:
            break
        hashtags.append(tweet[pos:pos_aux])
        tweet = tweet[:pos] + ' ' + tweet[pos_aux:]
        pos = tweet.find('#',pos + 1)
    return hashtags

In [10]:
print(get_hashtags("Body Language Analysis No.4303: Donald Trump, G7 Summit, Women's Empowerment, and Rage -  #Nonverbal &  #EmotionalIntelligence •   •  #DonaldTrump #AngelaMerkel #Anger #BehaviorAnalysis #BodyLanguage #BodyLanguageExpert #Analysis #EQ #G7 #G7Summit"))

['#Nonverbal', '#EmotionalIntelligence', '#DonaldTrump', '#AngelaMerkel', '#Anger', '#BehaviorAnalysis', '#BodyLanguage', '#BodyLanguageExpert', '#Analysis', '#EQ', '#G7']


In [11]:
def get_mentions(tweet):
    mentions = []
    pos = tweet.find('@')
    while pos != -1:
        pos_aux = tweet.find(" ",pos)
        if pos_aux == -1:
            break
        mentions.append(tweet[pos:pos_aux])
        tweet = tweet[:pos] + ' ' + tweet[pos_aux:]
        pos = tweet.find('@',pos + 1)
    return mentions

In [12]:
print(get_mentions("May God Bless you and Bless God for  #DonaldTrump @lindathomas102 @louisa_ip @maga_417 @MarcGriff89 @MarjorieLoy1@Maximus_Paulus @MC_Mad_Man @mgw81180 @MrSteveRangel @MyMountainTop @Namashary @netteKnows @NotUnderdog @NYKchi88 @nykon187@ofarther"))

['@lindathomas102', '@louisa_ip', '@maga_417', '@MarcGriff89', '@MarjorieLoy1@Maximus_Paulus', '@MC_Mad_Man', '@mgw81180', '@MrSteveRangel', '@MyMountainTop', '@Namashary', '@netteKnows', '@NotUnderdog', '@NYKchi88']


In [13]:
dates = []
user = []
status = []
comments = []
likes = []
retweets = []
tweet = []
tweet_no_html = []
hashtags = []
mentions = []
for tweet_status in tweets_list:
    pos = tweet_status.find(',')
    dates.append(tweet_status[:pos])
    
    tweet_status = tweet_status[pos + 1:].strip()
    pos = tweet_status.find(',')
    user.append(tweet_status[:pos])
    
    tweet_status = tweet_status[pos + 1:].strip()
    pos = tweet_status.find(',')
    status.append(tweet_status[:pos])
    
    tweet_status = tweet_status[pos + 1:].strip()
    pos = tweet_status.find(',')
    comments.append(tweet_status[:pos])
    
    tweet_status = tweet_status[pos + 1:].strip()
    pos = tweet_status.find(',')
    likes.append(tweet_status[:pos])
    
    tweet_status = tweet_status[pos + 1:].strip()
    pos = tweet_status.find(',')
    retweets.append(tweet_status[:pos])
        
    tweet_status = tweet_status[pos + 1:].strip()    
    soup = BeautifulSoup(add_space_between_a_tags(tweet_status),'lxml')
    
    tweet_status_no_html = soup.text
    
    tweet.append(tweet_status_no_html)
    
    pos_2 = tweet_status_no_html.find('pic.twitter.com/')
    tweet_status_no_html = tweet_status_no_html[:pos_2].strip()
    pos_3 = tweet_status_no_html.find('http')
    while pos_3 != -1:        
        tweet_status_no_html = tweet_status_no_html[:pos_3 - 1] + ' ' + tweet_status_no_html[pos_3:]
        pos_3 = tweet_status_no_html.find('http',pos_3 + 1)
    tweet_status_no_html = re.sub(r"http\S+", "", tweet_status_no_html)
    tweet_status_no_html = tweet_status_no_html.strip().replace("\xa0","")
    tweet_no_html.append(tweet_status_no_html)
    
    hashtags.append(get_hashtags(tweet_status_no_html))
    mentions.append(get_mentions(tweet_status_no_html))

In [14]:
len(dates)

10244

In [15]:
x = randint(0, len(dates))
print(x)
print(dates[x],user[x],status[x],comments[x],likes[x],retweets[x],tweet[x],tweet_no_html[x],hashtags[x],mentions[x],end="\n")

2672
2018-02-09 ryanmauro https://twitter.com/ryanmauro/status/962046583788326912 2 12 5 #DonaldTrump  supporters /  #GOP  love news of  #UraniumOneScandal #Democrats  love stories about  #CarterPage  &  #Manafort .How hard is it to see that  #Russia  exploited our hyper-partisanship and targeted both sides, just as intel community said?Partisanship is blinding us. #DonaldTrump  supporters /  #GOP  love news of  #UraniumOneScandal #Democrats  love stories about  #CarterPage  &  #Manafort .How hard is it to see that  #Russia  exploited our hyper-partisanship and targeted both sides, just as intel community said?Partisanship is blinding us ['#DonaldTrump', '#GOP', '#UraniumOneScandal', '#Democrats', '#CarterPage', '#Manafort', '#Russia'] []


In [16]:
index = 0
for i in tweet_no_html:
    print(index,':',i)
    index = index + 1

0 : Dear  #DonaldTrump
1 : #America  demands  #TrumpShowUsYourPenis #DonaldTrump #MAGA
2 : Enough.  #DonaldTrump
3 : #DonaldTrump  stop blaming PAK... and PAK Should  #StopAmericanSupplies
4 : Pakistan will Not Do More !!  #NoMoreTrump #DonaldTrump #StopAmericanSupplies
5 : #DonaldTrump #DonaldTrumpsPak  Short term memory loss syndrome OR Bipolar disorder?
6 : Pakistan is not Fighting for Money : DG ISPR #NoMoreTrump #StopAmericanSupplies #DonaldTrump
7 : Dear  #DonaldTrump  you know fairly after March 2018.......you will never be able to threatened State of Pakistan ever again.......So now  #NoMoreTrump
8 : So, the President of America doesn't know that the exeggerated figure of $33 billion in Coalition Support Fund "IS NOT AID".  #DonaldTrump
9 : Only problem is .... #DonaldTrump  can't be disappeare
10 : #DonaldTrump  is trending top in  #Pakistan  right now and not for any good reason
11 : Becoz we are busy in lifting "Mukka" from Mukka chawk..all 33 billion dollars are used to van

960 : No Shit,  #donaldtrump  Is Racist
961 : DeAr BLACK Africans!!! You deserve what ever stupid people like the  #crackhead #DonaldTRUMP  refers to you...
962 : 'mum why did  #DonaldTrump  say he wants people from  #Norway  to go to America?''because he only wants white people to go there.''Oh. why?''Because he is a racist' @realDonaldTrump #shitholecountry
963 : as does Paul Ryan folks...  @SpeakerRyan #donaldtrump #trump #trumptrain #maga #WhiteSupremacy  Trump The Pig is fried
964 : UN rights office decries  #DonaldTrump 's reported remarks as 'racist'  #President #UnitedNations ...  …
965 : Hmmm okay  #donaldtrump  #celebrity #celebrities #trending #trendingtopic #whitehouse …
966 : Trump lawyer arranged pre-election hush  #money  for porn star: report   #global #donaldtrump
967 : 
968 : Donald bumbohole dump  #DonaldTrump #shithole
969 : #Nicaragua : For Arrogant  #DonaldTrump , probably just another  #shithole . However,  #WindPower  everywhere at  #LakeOmetepe . Very forward l

1126 : If  #DonaldTrump  is 239 pounds, I'm the new face of  @lorealparis  shampo
1127 : Corrupt  #KirstjenNielsen ,  #DHSSecretary , LIES like  #DonaldTrump  & others in  #TrumpAdministration .  @SecNielsen  /  #Nielsen  is a disgrace. Unacceptable! #Trump  said  #ShitholeCountries . Trump is a  #racist  &  #WhiteSupremacist . @WhiteHouse @CNN @AP @nytimes @thehill @washingtonpost
1128 : She has a shithole mouth! Ana Navarro Says Trump Must Pass DACA To Prove He Isn’t Racist... Then Calls Him A Vulgar Word In Spanish  … #AnaNavarro #DonaldTrump  via  @BarracudaMama
1129 : GAIN FREE FOLLOWERS  Follow everyone who RT or LIKES this Follow  @mysexygirls001 @StefaniTarrago @skyebluewantsu @Sexy_RheaRey @ShawnaLeneeShow #TrapaDrive #1DDrive #FollowBack #follo4follo #PORN #Videos #Trending #DonaldTrump #StormyDaniels #BreakingNews
1130 : No way does  #Bannon  do time for  #DonaldTrump , especially not now.Tick Tock.. #MuellerTime #TrumpRussia @LBC #bbcpm
1131 : Joe Biden Explains Why Trump S

2293 : WATCH: People Hate Lines From Obama’s SOTU — When They’re Told It’s From Trump’s! #IdiotsUnited #LackOfEducation #DonaldTrump #SOTU #BluestarZone …
2294 : Piers Morgan’s not happy about this picture – the funniest 21 responses online  … #PiersMorgan #DonaldTrump
2295 : #OMFG  These are showing up all over the place.  The  #usa  really loathes you,  #DonaldTrump .  You will be remembered as the  #WorstPresidentEver
2296 : FLASHBACK: Valerie Jarrett Kept A ‘Payback List’ Of Obama’s Enemies! #DonaldTrump #RedWaveRising2018 #GreatAwakening #BluestarZone …
2297 : Nunes Hints Second Memo Will Expose John Kerry!!Kerry You Are Next! #TraitorMcCain #HumanScum #GreatAwakening #DonaldTrump #BluestarZone …
2298 : If  #Trump  didn’t grant approval, Putin is running the show & doesn’t need anyone’s ok.Or #DonaldTrump  is enforcing  #RussianSanctions  like they’re a joke to him.Or both. #DemForce #TrumpRussia #MuellerInvestigation #TrumpRussiaConspiracy #SaturdayMorning #GOP @DNC #AMJoy …
2299

3459 : » No Food or Blankets for  #Palestinian  Detainees at Etzion– IMEMC News  … #Nakba #bringbackourboys #bringbackourgirls #FreePalestine  #Palestine #BoycottIsrael #BDS #CNN #BBC #FoxNews #ABC #NBC #CBS #DonaldTrump #NikkiHaley #Apartheid #Israel #Netanyahu
3460 : If the only idea  #DonaldTrump  gets out of today's  #ListeningSession  is to foolishly arm teachers, then he wasn't really listening  #GunReformNow #ParklandStudentsSpeak
3461 : Mueller asking if Manafort promised banker White House job in return for loans #PaulManafort #Mueller #RobertMueller #WhiteHouse #Trump #DonaldTrump …
3462 : #Happy420 #DonaldTrump  gets very high!    The secret life of Trump!  #Comedy #Parody  Toke kids! Y
3463 : When you need a note to remind you to sayI HEAR YOU.....YOU FREAKING LOST ME.  #DonaldTrump #ParklandStudentsSpeak
3464 : #DonaldTrump  suggests putting more guns in schools to fight  #GunViolence ?!?  #ConcealedCarry #SchoolShootings #Florida Cartoon:  @theheraldsun #guncrisis #GunCon

...

5792 : Thats because  #DonaldTrump  (  @potus  ) is a classless cockroach. #WhiteHouse #FakePresident #PutinPuppet #WorstPresidentEver …
5793 : 3:33  #POLL : What’s The Most Reliable Source Of Information? #FoxNews #SinclairBroadcasting #Sinclair #BoycottSinclair #Trump #SinclairStrike #Fox #DonaldTrump
5794 : You wanna talk to your daddy  #DonaldTrump  about the importance of exercise? Nah, didn't think so.
5795 : So true! In my house my opinion did not matter. It shouldn’t have. As a child we have uninformed opinions. Nothing has changed.  #MAGA @realDonaldTrump #Trump #Opinion #POTUS #LoveAChristian #Trumpville #DonaldTrump #RedWaveRising2018 #LoveYourKids …
5796 : #DonaldTrump 's wall promise was no more serious than anything else that comes out of his mouth. The president's antipathy toward Latinos and other non-whites is genuine, but his ability to follow through on building a border wall is pure counterfeit.
5797 : If  #DonaldTrump  keeps this promise, he could yet save  #Americ

6959 : When in doubt, target the most vulnerable!  #IMHO , that’s exactly what  #DonaldTrump  is doing as he violates his campaign promise to transgender people  @GreaterBoston
6960 : If the presidential elections  #Election2016  were held today, would you vote for  #DonaldTrump  or  #HillaryClinton  ?   #Republicans #Democrat #MAGA #POTUS #Election2018    Vote & Retweet!!
6961 : "This week is a microcosm of  @realDonaldTrump 's America:A white shooter.People of color brutally murdered.A black, gunless hero saving strangers.A silent white President." … #TravisReinking  terrorist #DonaldTrump  disgrace #JamesShawJrIsAHero
6962 : #DonaldTrump  is corrupt and unfit, putting this country and it’s safety at risk.  #TrumpMustGo
6963 : It starts. Media begins bullying  #KanyeWest  for his free thought and respect for  #CandaceOwens  and  #DonaldTrump
6964 : "It seems Trump is using Macron as one of his characters for celebrity apprentice"  @JCBua  discusses  #EmmanuelMacron  being given the h

8125 : How  #RobertMueller  knew  #Ford  Motor Company rejected  #MichaelCohen ’s request for a  #DonaldTrump  bribe  …  via  @PalmerReport
8126 : we are NOT talking about  #satanists ,  #wiccans ,  #shamans , or various forms of “white magic.” We are talking about  #luciferianism .  #DonaldTrump  got involved in the  #occult  decades ago - NOT because he desired a  #spiritual  walk, after all there’s nothing spiritual about him, bu
8127 : Let’s remind everyone, nothing has changed!!  @realDonaldTrump  is still a criminal along with his  #TrumpCrimeFamily . @POTUS  is trying to distract us.... leopards don’t change their spots... either does  #DonaldTrump
8128 : "I got this" -  #donaldtrump
8129 : #DPRK  will hold a ceremony for the dismantling of its  #nuclear  test site on May 23-25   . An indication that   #DonaldTrump  is indeed “a very stable genius” as he said in one of his own recent tweets?
8130 : #NorthKorea  details plans to dismantle nuclear test site ahead of  #KimJong -un 

8959 : That’s exactly the point.  The extremely unconventional  #ElonMusk  and  #DonaldTrump  have a much better sense of the national mood than the media culture has
8960 : possibilities: 1.)  #DonaldTrump  and some of his friends are  #moneylaundering  through a  #restaurant  in  #LosAngeles  (VERY likely), 2.)  #Trump ,  #Pompeo ,  #Stone ,  #Hannity ,  #Giuliani , and everybody else involved in  #TrumpsTraffickingRing  is using a  #mexican  restaurant as a cover t
8961 : We will post more of  #donaldTrump  and  #IvankaTrump ’s sock businesses, addresses, and numbers in the next few days. But we felt because of everybody asking the question  #WhereAreTheChidren  that this was important to bring up this morning. The facts we just posted point to severa
8962 : A  #Taliban  roadside mine killed Haji Gul Nabi a resident of  #Logar  province in  #Afghanistan  who had honored US President  #DonaldTrump  with the medal of bravery for his anti-Pakistan policy and cutting off military aid to

10125 : I'm crying #DonaldTrump
10126 : Love him or hate him.  #DonaldTrump  seems to be doing a pretty decent job so fa
10127 : #ROCKETMAN  is killin me...  Need to get on that  #DonaldTrump  level. HA!
10128 : The greatest episode of the office That never was.  @rickygervais #DonaldTrump #TrumpKimSummit
10129 : #FREEBILLCOSBY  DONT JUST LIKE (this vid)CLICK LINK IN BIO &  TAG TAG TAG  #spinrilla #soundcloudrapper #trending #djakademiks #wshh #hiphop #worldstarhiphop #freemeek #lyrics #tbt #mixtape #trap #music  #1017  #LA #Cali #realrap #russia #donaldtrump #follow4follow
10130 : If this life isn’t a simulation, I’ll be fucked.  #DonaldTrump #KimJongUn
10131 : #TrumpKimSumit #DonaldTrump  Is One Sick Fu*k❝Boy, Look At That View.   Wouldn’t That Make A Great Condo?❞❝You Could Have The Best Hotels In The World    Right There…❞❝Think Of It From A Real Estate Perspective…❞      #Trump
10132 : Historic Talk Pencil Sketch by me :)  #TrumpKimSummit #SingaporeSummit #DonaldTrump #KimJongUn
1

In [17]:
import nltk
import re
import time
from collections import defaultdict
from configparser import ConfigParser
from gensim import corpora, models, similarities
from nltk.tokenize import RegexpTokenizer
from string import digits
nltk.download('stopwords')


/home/miguel/anaconda3/lib/python3.6/site-packages/scipy/sparse/sparsetools.py:21: DeprecationWarning: `scipy.sparse.sparsetools` is deprecated!
scipy.sparse.sparsetools is a private module for scipy.sparse, and should not be used.
  _deprecated()


[nltk_data] Downloading package stopwords to /home/miguel/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [18]:

tokenizer = RegexpTokenizer(r'\w+')
documents = [ tokenizer.tokenize(t.lower()) for t in tweet_no_html ]

In [19]:
#def clean_tweet(tweet):
    
#def tokenize(tweet):
    

In [20]:
#tokenized_and_clean_tweets = [tokenize(clean_tweet(tweet)) for tweet in tweet_no_html]

In [21]:
documents

[['dear', 'donaldtrump'],
 ['america', 'demands', 'trumpshowusyourpenis', 'donaldtrump', 'maga'],
 ['enough', 'donaldtrump'],
 ['donaldtrump',
  'stop',
  'blaming',
  'pak',
  'and',
  'pak',
  'should',
  'stopamericansupplies'],
 ['pakistan',
  'will',
  'not',
  'do',
  'more',
  'nomoretrump',
  'donaldtrump',
  'stopamericansupplies'],
 ['donaldtrump',
  'donaldtrumpspak',
  'short',
  'term',
  'memory',
  'loss',
  'syndrome',
  'or',
  'bipolar',
  'disorder'],
 ['pakistan',
  'is',
  'not',
  'fighting',
  'for',
  'money',
  'dg',
  'ispr',
  'nomoretrump',
  'stopamericansupplies',
  'donaldtrump'],
 ['dear',
  'donaldtrump',
  'you',
  'know',
  'fairly',
  'after',
  'march',
  '2018',
  'you',
  'will',
  'never',
  'be',
  'able',
  'to',
  'threatened',
  'state',
  'of',
  'pakistan',
  'ever',
  'again',
  'so',
  'now',
  'nomoretrump'],
 ['so',
  'the',
  'president',
  'of',
  'america',
  'doesn',
  't',
  'know',
  'that',
  'the',
  'exeggerated',
  'figure',
 

In [22]:
unigrams = [ w for doc in documents for w in doc if len(w)==1]
bigrams  = [ w for doc in documents for w in doc if len(w)==2]

In [23]:
trump_stop_words = ['trump','donald','donaldtrump','realdonaldtrump']

In [24]:
stoplist  = set(nltk.corpus.stopwords.words("english") + 
                 unigrams + bigrams + trump_stop_words)

In [67]:
documents = [[token for token in doc if token not in stoplist and not token.isdigit()] for doc in documents]

In [68]:
documents

[['dear'], ['america', 'demands', 'maga', 'trumpshowusyourpenis'], ['enough'], ['blaming', 'pak', 'pak', 'stop', 'stopamericansupplies'], ['nomoretrump', 'pakistan', 'stopamericansupplies'], ['bipolar', 'disorder', 'donaldtrumpspak', 'loss', 'memory', 'short', 'syndrome', 'term'], ['fighting', 'ispr', 'money', 'nomoretrump', 'pakistan', 'stopamericansupplies'], ['able', 'dear', 'ever', 'fairly', 'know', 'march', 'never', 'nomoretrump', 'pakistan', 'state', 'threatened'], ['aid', 'america', 'billion', 'coalition', 'exeggerated', 'figure', 'fund', 'know', 'president', 'support'], ['disappeare', 'problem'], ['good', 'pakistan', 'reason', 'right', 'top', 'trending'], ['becoz', 'billion', 'busy', 'chawk', 'coz', 'dollars', 'dont', 'frm', 'karachiwe', 'lifting', 'mqm', 'mqm', 'mukka', 'mukka', 'need', 'say', 'still', 'used', 'vanish'], ['americans', 'anyone', 'chance', 'democracy', 'get', 'gop', 'hands', 'happy', 'insider', 'knew', 'markets', 'panic', 'rest', 'rich', 'street', 'suffer', 'tra

In [27]:
for doc in documents:
    doc.sort()

dictionary = corpora.Dictionary(documents)
dictionary.compactify()
corpus = [dictionary.doc2bow(doc) for doc in documents]

In [72]:
[[(dictionary[id], freq) for id, freq in cp] for cp in corpus[:10]]

[[('dear', 1)], [('america', 1), ('demands', 1), ('maga', 1), ('trumpshowusyourpenis', 1)], [('enough', 1)], [('blaming', 1), ('pak', 2), ('stop', 1), ('stopamericansupplies', 1)], [('stopamericansupplies', 1), ('nomoretrump', 1), ('pakistan', 1)], [('bipolar', 1), ('disorder', 1), ('donaldtrumpspak', 1), ('loss', 1), ('memory', 1), ('short', 1), ('syndrome', 1), ('term', 1)], [('stopamericansupplies', 1), ('nomoretrump', 1), ('pakistan', 1), ('fighting', 1), ('ispr', 1), ('money', 1)], [('dear', 1), ('nomoretrump', 1), ('pakistan', 1), ('able', 1), ('ever', 1), ('fairly', 1), ('know', 1), ('march', 1), ('never', 1), ('state', 1), ('threatened', 1)], [('america', 1), ('know', 1), ('aid', 1), ('billion', 1), ('coalition', 1), ('exeggerated', 1), ('figure', 1), ('fund', 1), ('president', 1), ('support', 1)], [('disappeare', 1), ('problem', 1)]]

In [65]:
lda_model =  models.ldamodel.LdaModel(corpus, num_topics=30)
pyLDAvis.enable_notebook()
pyLDAvis.gensim.prepare(lda_model, corpus, dictionary)

/home/miguel/anaconda3/lib/python3.6/site-packages/pyLDAvis/_prepare.py:257: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=True'.

To retain the current behavior and silence the warning, pass sort=False

  return pd.concat([default_term_info] + list(topic_dfs))


PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
1     -0.016026  0.108662       1        1  4.407635
9     -0.045388  0.089862       2        1  4.292898
25    -0.063680 -0.085022       3        1  3.980987
28     0.009123  0.073489       4        1  3.963221
22     0.017271  0.106448       5        1  3.885792
2      0.170006  0.028179       6        1  3.842524
4     -0.063575  0.016396       7        1  3.817530
26    -0.049731  0.037467       8        1  3.651236
19     0.269087 -0.013459       9        1  3.570692
20     0.016394  0.089033      10        1  3.562818
0      0.250129 -0.045693      11        1  3.548870
17    -0.027529  0.070113      12        1  3.514201
10    -0.027286  0.041364      13        1  3.507705
15    -0.039874  0.011141      14        1  3.493865
29    -0.039172  0.058725      15        1  3.427253
11     0.000628 -0.142872      16        1  3.393238
27    -0.071675  0.008855      17        1  3.233396
8      0.009285 -0.061292      18        1  3.191390
14    -0.012519 -0.058511      19        1  3.126070
18     0.060480  0.045211      20        1  3.069882
5     -0.047804  0.098690      21        1  3.016922
12    -0.026768 -0.009866      22        1  2.919073
3     -0.044286  0.015160      23        1  2.847243
6     -0.040084 -0.039640      24        1  2.822773
16    -0.052626 -0.027676      25        1  2.819746
24    -0.038204 -0.102688      26        1  2.797109
13     0.066916 -0.030768      27        1  2.783244
21    -0.028920 -0.149894      28        1  2.769402
23    -0.062968 -0.029564      29        1  2.373888
7     -0.071206 -0.101849      30        1  2.369401, topic_info=      Category        Freq                   Term       Total  loglift  \
term                                                                     
629    Default  777.000000              kimjongun  777.000000  30.0000   
12422  Default  361.000000              singapore  361.000000  29.0000   
7794   Default  231.000000                 summit  231.000000  28.0000   
21466  Default  632.000000         trumpkimsummit  632.000000  27.0000   
630    Default  292.000000             northkorea  292.000000  26.0000   
5031   Default  244.000000                 canada  244.000000  25.0000   
22307  Default  419.000000        singaporesummit  419.000000  24.0000   
264    Default  208.000000                  peace  208.000000  23.0000   
1731   Default  205.000000                  north  205.000000  22.0000   
1730   Default  207.000000                  korea  207.000000  21.0000   
239    Default  221.000000                    kim  221.000000  20.0000   
871    Default  236.000000                meeting  236.000000  19.0000   
2224   Default  159.000000               historic  159.000000  18.0000   
562    Default  172.000000                    god  172.000000  17.0000   
1380   Default  172.000000                cartoon  172.000000  16.0000   
4988   Default  144.000000           robertdeniro  144.000000  15.0000   
3129   Default  137.000000                   hope  137.000000  14.0000   
3015   Default  128.000000                   body  128.000000  13.0000   
3      Default  673.000000                   maga  673.000000  12.0000   
2230   Default  123.000000               analysis  123.000000  11.0000   
314    Default  203.000000                leaders  203.000000  10.0000   
653    Default  320.000000                 russia  320.000000   9.0000   
5544   Default  147.000000          justintrudeau  147.000000   8.0000   
3019   Default  115.000000               language  115.000000   7.0000   
169    Default  224.000000                foxnews  224.000000   6.0000   
1118   Default  175.000000                 leader  175.000000   5.0000   
222    Default  379.000000                  world  379.000000   4.0000   
3021   Default  110.000000              nonverbal  110.000000   3.0000   
1512   Default  150.000000               

In [61]:
print(lda_model.get_topic_terms(29))

[(218, 0.018109327), (26, 0.01380417), (4360, 0.013021712), (5222, 0.011655531), (602, 0.0116157), (1584, 0.009837298), (834, 0.009588984), (7138, 0.008242381), (981, 0.008114909), (198, 0.0077617397)]


In [66]:
x=lda_model.show_topics(num_topics=12, num_words=5,formatted=False)
topics_words = [(tp[0], [wd[0] for wd in tp[1]]) for tp in x]

#Below Code Prints Topics and Words
for topic,words in topics_words:
    print(str(topic)+ "::"+ str(words))
print()

#Below Code Prints Only Words 
for topic,words in topics_words:
    print(" ".join(words))

14::['1580', '37', '4172', '426', '871']
21::['1380', '3015', '2230', '3019', '3021']
16::['85', '1567', '1276', '1768', '3792']
29::['1087', '141', '262', '5362', '4360']
19::['629', '630', '22307', '21466', '37']
24::['3129', '1706', '653', '6333', '1619']
17::['1028', '1503', '12183', '615', '4052']
8::['264', '375', '222', '14881', '2830']
27::['5621', '271', '443', '446', '15328']
23::['3061', '198', '953', '1355', '304']
18::['14592', '21466', '3728', '3416', '938']
11::['5031', '446', '653', '171', '535']

1580 37 4172 426 871
1380 3015 2230 3019 3021
85 1567 1276 1768 3792
1087 141 262 5362 4360
629 630 22307 21466 37
3129 1706 653 6333 1619
1028 1503 12183 615 4052
264 375 222 14881 2830
5621 271 443 446 15328
3061 198 953 1355 304
14592 21466 3728 3416 938
5031 446 653 171 535


In [34]:
lda.per_word_topics

False